In [2]:
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
from policyengine_us import Simulation
from policyengine_core.reforms import Reform

/Users/pavelmakarchuk/anaconda3/envs/pe/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


# SALT and AMT Case Study

This notebook analyzes the impact of different tax policies on households in high-tax states (NY, NJ, CA, PA) at different income levels. We'll compare:

1. Current law
2. Current policy
3. Current policy + SALT capped at $25k single/$50k married filing jointly

In [9]:

current_policy = Reform.from_dict(
    {
        "gov.irs.income.bracket.rates.2": {"2026-01-01.2100-12-31": 0.12},
        "gov.irs.income.bracket.rates.3": {"2026-01-01.2100-12-31": 0.22},
        "gov.irs.income.bracket.rates.4": {"2026-01-01.2100-12-31": 0.24},
        "gov.irs.income.bracket.rates.5": {"2026-01-01.2100-12-31": 0.32},
        "gov.irs.income.bracket.rates.7": {"2026-01-01.2100-12-31": 0.37},
        "gov.irs.deductions.qbi.max.rate": {"2026-01-01.2100-12-31": 0.2},
        "gov.irs.income.exemption.amount": {"2026-01-01.2100-12-31": 0},
        "gov.irs.deductions.qbi.max.w2_wages.rate": {"2026-01-01.2100-12-31": 0.5},
        "gov.irs.deductions.standard.amount.JOINT": {
            "2026-01-01.2026-12-31": 30600,
            "2027-01-01.2027-12-31": 31225,
            "2028-01-01.2028-12-31": 31825,
            "2029-01-01.2029-12-31": 32425,
            "2030-01-01.2030-12-31": 33050,
            "2031-01-01.2031-12-31": 33725,
            "2032-01-01.2032-12-31": 34400,
            "2033-01-01.2033-12-31": 35075,
            "2034-01-01.2034-12-31": 35775,
            "2035-01-01.2035-12-31": 36500,
        },
        "gov.irs.credits.ctc.amount.base[0].amount": {"2026-01-01.2100-12-31": 2000},
        "gov.irs.deductions.standard.amount.SINGLE": {
            "2026-01-01.2026-12-31": 15300,
            "2027-01-01.2027-12-31": 15600,
            "2028-01-01.2028-12-31": 15900,
            "2029-01-01.2029-12-31": 16225,
            "2030-01-01.2030-12-31": 16525,
            "2031-01-01.2031-12-31": 16850,
            "2032-01-01.2032-12-31": 17200,
            "2033-01-01.2033-12-31": 17550,
            "2034-01-01.2034-12-31": 17900,
            "2035-01-01.2035-12-31": 18250,
        },
        "gov.irs.income.amt.exemption.amount.JOINT": {
            "2026-01-01.2026-12-31": 139850,
            "2027-01-01.2027-12-31": 142675,
            "2028-01-01.2028-12-31": 145425,
            "2029-01-01.2029-12-31": 148200,
            "2030-01-01.2030-12-31": 151100,
            "2031-01-01.2031-12-31": 154100,
            "2032-01-01.2032-12-31": 157150,
            "2033-01-01.2033-12-31": 160300,
            "2034-01-01.2034-12-31": 163525,
            "2035-01-01.2035-12-31": 166850,
        },
        "gov.irs.income.bracket.thresholds.3.JOINT": {
            "2026-01-01.2026-12-31": 210950,
            "2027-01-01.2027-12-31": 215225,
            "2028-01-01.2028-12-31": 219375,
            "2029-01-01.2029-12-31": 223525,
            "2030-01-01.2030-12-31": 227925,
            "2031-01-01.2031-12-31": 232425,
            "2032-01-01.2032-12-31": 237075,
            "2033-01-01.2033-12-31": 241825,
            "2034-01-01.2034-12-31": 246675,
            "2035-01-01.2035-12-31": 251675,
        },
        "gov.irs.income.bracket.thresholds.4.JOINT": {
            "2026-01-01.2026-12-31": 402725,
            "2027-01-01.2027-12-31": 410875,
            "2028-01-01.2028-12-31": 418800,
            "2029-01-01.2029-12-31": 426725,
            "2030-01-01.2030-12-31": 435125,
            "2031-01-01.2031-12-31": 443725,
            "2032-01-01.2032-12-31": 452575,
            "2033-01-01.2033-12-31": 461650,
            "2034-01-01.2034-12-31": 470925,
            "2035-01-01.2035-12-31": 480450,
        },
        "gov.irs.income.bracket.thresholds.5.JOINT": {
            "2026-01-01.2026-12-31": 511400,
            "2027-01-01.2027-12-31": 521775,
            "2028-01-01.2028-12-31": 531850,
            "2029-01-01.2029-12-31": 541925,
            "2030-01-01.2030-12-31": 552575,
            "2031-01-01.2031-12-31": 563500,
            "2032-01-01.2032-12-31": 574725,
            "2033-01-01.2033-12-31": 586250,
            "2034-01-01.2034-12-31": 598050,
            "2035-01-01.2035-12-31": 610125,
        },
        "gov.irs.income.bracket.thresholds.6.JOINT": {
            "2026-01-01.2026-12-31": 767125,
            "2027-01-01.2027-12-31": 782650,
            "2028-01-01.2028-12-31": 797775,
            "2029-01-01.2029-12-31": 812875,
            "2030-01-01.2030-12-31": 828850,
            "2031-01-01.2031-12-31": 845250,
            "2032-01-01.2032-12-31": 862100,
            "2033-01-01.2033-12-31": 879350,
            "2034-01-01.2034-12-31": 897050,
            "2035-01-01.2035-12-31": 915200,
        },
        "gov.irs.credits.ctc.amount.adult_dependent": {"2026-01-01.2100-12-31": 500},
        "gov.irs.income.amt.exemption.amount.SINGLE": {
            "2026-01-01.2026-12-31": 89925,
            "2027-01-01.2027-12-31": 91750,
            "2028-01-01.2028-12-31": 93525,
            "2029-01-01.2029-12-31": 95300,
            "2030-01-01.2030-12-31": 97150,
            "2031-01-01.2031-12-31": 99075,
            "2032-01-01.2032-12-31": 101050,
            "2033-01-01.2033-12-31": 103075,
            "2034-01-01.2034-12-31": 105150,
            "2035-01-01.2035-12-31": 107275,
        },
        "gov.irs.income.bracket.thresholds.3.SINGLE": {
            "2026-01-01.2026-12-31": 105475,
            "2027-01-01.2027-12-31": 107600,
            "2028-01-01.2028-12-31": 109700,
            "2029-01-01.2029-12-31": 111775,
            "2030-01-01.2030-12-31": 113950,
            "2031-01-01.2031-12-31": 116225,
            "2032-01-01.2032-12-31": 118525,
            "2033-01-01.2033-12-31": 120900,
            "2034-01-01.2034-12-31": 123350,
            "2035-01-01.2035-12-31": 125825,
        },
        "gov.irs.income.bracket.thresholds.4.SINGLE": {
            "2026-01-01.2026-12-31": 201350,
            "2027-01-01.2027-12-31": 205425,
            "2028-01-01.2028-12-31": 209400,
            "2029-01-01.2029-12-31": 213375,
            "2030-01-01.2030-12-31": 217550,
            "2031-01-01.2031-12-31": 221875,
            "2032-01-01.2032-12-31": 226275,
            "2033-01-01.2033-12-31": 230825,
            "2034-01-01.2034-12-31": 235475,
            "2035-01-01.2035-12-31": 240225,
        },
        "gov.irs.income.bracket.thresholds.5.SINGLE": {
            "2026-01-01.2026-12-31": 255700,
            "2027-01-01.2027-12-31": 260875,
            "2028-01-01.2028-12-31": 265925,
            "2029-01-01.2029-12-31": 270950,
            "2030-01-01.2030-12-31": 276275,
            "2031-01-01.2031-12-31": 281750,
            "2032-01-01.2032-12-31": 287375,
            "2033-01-01.2033-12-31": 293125,
            "2034-01-01.2034-12-31": 299025,
            "2035-01-01.2035-12-31": 305075,
        },
        "gov.irs.income.bracket.thresholds.6.SINGLE": {
            "2026-01-01.2026-12-31": 639300,
            "2027-01-01.2027-12-31": 652250,
            "2028-01-01.2028-12-31": 664825,
            "2029-01-01.2029-12-31": 677425,
            "2030-01-01.2030-12-31": 690725,
            "2031-01-01.2031-12-31": 704400,
            "2032-01-01.2032-12-31": 718425,
            "2033-01-01.2033-12-31": 732825,
            "2034-01-01.2034-12-31": 747575,
            "2035-01-01.2035-12-31": 762675,
        },
        "gov.irs.deductions.itemized.casualty.active": {"2026-01-01.2100-12-31": False},
        "gov.irs.deductions.standard.amount.SEPARATE": {
            "2026-01-01.2026-12-31": 15300,
            "2027-01-01.2027-12-31": 15600,
            "2028-01-01.2028-12-31": 15900,
            "2029-01-01.2029-12-31": 16225,
            "2030-01-01.2030-12-31": 16525,
            "2031-01-01.2031-12-31": 16850,
            "2032-01-01.2032-12-31": 17200,
            "2033-01-01.2033-12-31": 17550,
            "2034-01-01.2034-12-31": 17900,
            "2035-01-01.2035-12-31": 18250,
        },
        "gov.irs.deductions.qbi.max.w2_wages.alt_rate": {"2026-01-01.2100-12-31": 0.25},
        "gov.irs.deductions.qbi.phase_out.start.JOINT": {
            "2024-01-01.2024-12-31": 396450,
            "2025-01-01.2025-12-31": 400575,
            "2026-01-01.2026-12-31": 409800,
            "2027-01-01.2027-12-31": 418100,
            "2028-01-01.2028-12-31": 426175,
            "2029-01-01.2029-12-31": 434225,
            "2030-01-01.2030-12-31": 442775,
            "2031-01-01.2031-12-31": 451525,
            "2032-01-01.2032-12-31": 460525,
            "2033-01-01.2033-12-31": 469750,
            "2034-01-01.2034-12-31": 479200,
            "2035-01-01.2035-12-31": 488900,
        },
        "gov.irs.income.amt.exemption.amount.SEPARATE": {
            "2026-01-01.2026-12-31": 69925,
            "2027-01-01.2027-12-31": 71350,
            "2028-01-01.2028-12-31": 72725,
            "2029-01-01.2029-12-31": 74100,
            "2030-01-01.2030-12-31": 75550,
            "2031-01-01.2031-12-31": 77050,
            "2032-01-01.2032-12-31": 78575,
            "2033-01-01.2033-12-31": 80150,
            "2034-01-01.2034-12-31": 81775,
            "2035-01-01.2035-12-31": 83425,
        },
        "gov.irs.income.bracket.thresholds.3.SEPARATE": {
            "2026-01-01.2026-12-31": 105475,
            "2027-01-01.2027-12-31": 107600,
            "2028-01-01.2028-12-31": 109700,
            "2029-01-01.2029-12-31": 111775,
            "2030-01-01.2030-12-31": 113950,
            "2031-01-01.2031-12-31": 116225,
            "2032-01-01.2032-12-31": 118525,
            "2033-01-01.2033-12-31": 120900,
            "2034-01-01.2034-12-31": 123350,
            "2035-01-01.2035-12-31": 125825,
        },
        "gov.irs.income.bracket.thresholds.4.SEPARATE": {
            "2026-01-01.2026-12-31": 201350,
            "2027-01-01.2027-12-31": 205425,
            "2028-01-01.2028-12-31": 209400,
            "2029-01-01.2029-12-31": 213375,
            "2030-01-01.2030-12-31": 217550,
            "2031-01-01.2031-12-31": 221875,
            "2032-01-01.2032-12-31": 226275,
            "2033-01-01.2033-12-31": 230825,
            "2034-01-01.2034-12-31": 235475,
            "2035-01-01.2035-12-31": 240225,
        },
        "gov.irs.income.bracket.thresholds.5.SEPARATE": {
            "2026-01-01.2026-12-31": 255700,
            "2027-01-01.2027-12-31": 260875,
            "2028-01-01.2028-12-31": 265925,
            "2029-01-01.2029-12-31": 270950,
            "2030-01-01.2030-12-31": 276275,
            "2031-01-01.2031-12-31": 281750,
            "2032-01-01.2032-12-31": 287375,
            "2033-01-01.2033-12-31": 293125,
            "2034-01-01.2034-12-31": 299025,
            "2035-01-01.2035-12-31": 305075,
        },
        "gov.irs.income.bracket.thresholds.6.SEPARATE": {
            "2026-01-01.2026-12-31": 383550,
            "2027-01-01.2027-12-31": 391325,
            "2028-01-01.2028-12-31": 398875,
            "2029-01-01.2029-12-31": 406450,
            "2030-01-01.2030-12-31": 414425,
            "2031-01-01.2031-12-31": 422625,
            "2032-01-01.2032-12-31": 431050,
            "2033-01-01.2033-12-31": 439675,
            "2034-01-01.2034-12-31": 448525,
            "2035-01-01.2035-12-31": 457600,
        },
        "gov.irs.credits.ctc.phase_out.threshold.JOINT": {
            "2026-01-01.2100-12-31": 400000
        },
        "gov.irs.credits.ctc.refundable.individual_max": {
            "2026-01-01.2026-12-31": 1800,
            "2027-01-01.2027-12-31": 1800,
            "2028-01-01.2028-12-31": 1800,
            "2029-01-01.2029-12-31": 1900,
            "2030-01-01.2030-12-31": 1900,
            "2031-01-01.2031-12-31": 1900,
            "2032-01-01.2032-12-31": 2000,
            "2033-01-01.2033-12-31": 2000,
            "2034-01-01.2034-12-31": 2000,
            "2035-01-01.2035-12-31": 2000,
        },
        "gov.irs.deductions.qbi.phase_out.length.JOINT": {
            "2026-01-01.2100-12-31": 100000
        },
        "gov.irs.deductions.qbi.phase_out.start.SINGLE": {
            "2024-01-01.2024-12-31": 198225,
            "2025-01-01.2025-12-31": 200275,
            "2026-01-01.2026-12-31": 204900,
            "2027-01-01.2027-12-31": 209050,
            "2028-01-01.2028-12-31": 213075,
            "2029-01-01.2029-12-31": 217125,
            "2030-01-01.2030-12-31": 221375,
            "2031-01-01.2031-12-31": 225775,
            "2032-01-01.2032-12-31": 230275,
            "2033-01-01.2033-12-31": 234875,
            "2034-01-01.2034-12-31": 239600,
            "2035-01-01.2035-12-31": 244450,
        },
        "gov.irs.credits.ctc.phase_out.threshold.SINGLE": {
            "2026-01-01.2100-12-31": 200000
        },
        "gov.irs.deductions.qbi.phase_out.length.SINGLE": {
            "2026-01-01.2100-12-31": 50000
        },
        "gov.irs.deductions.itemized.charity.ceiling.all": {
            "2026-01-01.2100-12-31": 0.6
        },
        "gov.irs.deductions.itemized.limitation.agi_rate": {
            "2026-01-01.2100-12-31": np.inf
        },
        "gov.irs.deductions.qbi.phase_out.start.SEPARATE": {
            "2024-01-01.2024-12-31": 198225,
            "2025-01-01.2025-12-31": 200275,
            "2026-01-01.2026-12-31": 204900,
            "2027-01-01.2027-12-31": 209050,
            "2028-01-01.2028-12-31": 213075,
            "2029-01-01.2029-12-31": 217125,
            "2030-01-01.2030-12-31": 221375,
            "2031-01-01.2031-12-31": 225775,
            "2032-01-01.2032-12-31": 230275,
            "2033-01-01.2033-12-31": 234875,
            "2034-01-01.2034-12-31": 239600,
            "2035-01-01.2035-12-31": 244450,
        },
        "gov.irs.credits.ctc.phase_out.threshold.SEPARATE": {
            "2026-01-01.2100-12-31": 200000
        },
        "gov.irs.deductions.qbi.phase_out.length.SEPARATE": {
            "2026-01-01.2100-12-31": 50000
        },
        "gov.irs.credits.ctc.refundable.phase_in.threshold": {
            "2026-01-01.2100-12-31": 2500
        },
        "gov.irs.deductions.qbi.max.business_property.rate": {
            "2026-01-01.2100-12-31": 0.025
        },
        "gov.irs.income.amt.exemption.phase_out.start.JOINT": {
            "2026-01-01.2026-12-31": 1278575,
            "2027-01-01.2027-12-31": 1304475,
            "2028-01-01.2028-12-31": 1329675,
            "2029-01-01.2029-12-31": 1354850,
            "2030-01-01.2030-12-31": 1381475,
            "2031-01-01.2031-12-31": 1408825,
            "2032-01-01.2032-12-31": 1436875,
            "2033-01-01.2033-12-31": 1465650,
            "2034-01-01.2034-12-31": 1495150,
            "2035-01-01.2035-12-31": 1525375,
        },
        "gov.irs.deductions.standard.amount.SURVIVING_SPOUSE": {
            "2026-01-01.2026-12-31": 30600,
            "2027-01-01.2027-12-31": 31225,
            "2028-01-01.2028-12-31": 31825,
            "2029-01-01.2029-12-31": 32425,
            "2030-01-01.2030-12-31": 33050,
            "2031-01-01.2031-12-31": 33725,
            "2032-01-01.2032-12-31": 34400,
            "2033-01-01.2033-12-31": 35075,
            "2034-01-01.2034-12-31": 35775,
            "2035-01-01.2035-12-31": 36500,
        },
        "gov.irs.income.amt.exemption.phase_out.start.SINGLE": {
            "2026-01-01.2026-12-31": 639300,
            "2027-01-01.2027-12-31": 652250,
            "2028-01-01.2028-12-31": 664825,
            "2029-01-01.2029-12-31": 677425,
            "2030-01-01.2030-12-31": 690725,
            "2031-01-01.2031-12-31": 704400,
            "2032-01-01.2032-12-31": 718425,
            "2033-01-01.2033-12-31": 732825,
            "2034-01-01.2034-12-31": 747575,
            "2035-01-01.2035-12-31": 762675,
        },
        "gov.irs.deductions.standard.amount.HEAD_OF_HOUSEHOLD": {
            "2026-01-01.2026-12-31": 22950,
            "2027-01-01.2027-12-31": 23425,
            "2028-01-01.2028-12-31": 23875,
            "2029-01-01.2029-12-31": 24325,
            "2030-01-01.2030-12-31": 24800,
            "2031-01-01.2031-12-31": 25300,
            "2032-01-01.2032-12-31": 25800,
            "2033-01-01.2033-12-31": 26300,
            "2034-01-01.2034-12-31": 26825,
            "2035-01-01.2035-12-31": 27375,
        },
        "gov.irs.income.amt.exemption.amount.SURVIVING_SPOUSE": {
            "2026-01-01.2026-12-31": 139850,
            "2027-01-01.2027-12-31": 142675,
            "2028-01-01.2028-12-31": 145425,
            "2029-01-01.2029-12-31": 148200,
            "2030-01-01.2030-12-31": 151100,
            "2031-01-01.2031-12-31": 154100,
            "2032-01-01.2032-12-31": 157150,
            "2033-01-01.2033-12-31": 160300,
            "2034-01-01.2034-12-31": 163525,
            "2035-01-01.2035-12-31": 166850,
        },
        "gov.irs.income.bracket.thresholds.3.SURVIVING_SPOUSE": {
            "2026-01-01.2026-12-31": 210950,
            "2027-01-01.2027-12-31": 215225,
            "2028-01-01.2028-12-31": 219375,
            "2029-01-01.2029-12-31": 223525,
            "2030-01-01.2030-12-31": 227925,
            "2031-01-01.2031-12-31": 232425,
            "2032-01-01.2032-12-31": 237075,
            "2033-01-01.2033-12-31": 241825,
            "2034-01-01.2034-12-31": 246675,
            "2035-01-01.2035-12-31": 251675,
        },
        "gov.irs.income.bracket.thresholds.4.SURVIVING_SPOUSE": {
            "2026-01-01.2026-12-31": 402725,
            "2027-01-01.2027-12-31": 410875,
            "2028-01-01.2028-12-31": 418800,
            "2029-01-01.2029-12-31": 426725,
            "2030-01-01.2030-12-31": 435125,
            "2031-01-01.2031-12-31": 443725,
            "2032-01-01.2032-12-31": 452575,
            "2033-01-01.2033-12-31": 461650,
            "2034-01-01.2034-12-31": 470925,
            "2035-01-01.2035-12-31": 480450,
        },
        "gov.irs.income.bracket.thresholds.5.SURVIVING_SPOUSE": {
            "2026-01-01.2026-12-31": 511400,
            "2027-01-01.2027-12-31": 521775,
            "2028-01-01.2028-12-31": 531850,
            "2029-01-01.2029-12-31": 541925,
            "2030-01-01.2030-12-31": 552575,
            "2031-01-01.2031-12-31": 563500,
            "2032-01-01.2032-12-31": 574725,
            "2033-01-01.2033-12-31": 586250,
            "2034-01-01.2034-12-31": 598050,
            "2035-01-01.2035-12-31": 610125,
        },
        "gov.irs.income.bracket.thresholds.6.SURVIVING_SPOUSE": {
            "2026-01-01.2026-12-31": 767125,
            "2027-01-01.2027-12-31": 782650,
            "2028-01-01.2028-12-31": 797775,
            "2029-01-01.2029-12-31": 812875,
            "2030-01-01.2030-12-31": 828850,
            "2031-01-01.2031-12-31": 845250,
            "2032-01-01.2032-12-31": 862100,
            "2033-01-01.2033-12-31": 879350,
            "2034-01-01.2034-12-31": 897050,
            "2035-01-01.2035-12-31": 915200,
        },
        "gov.irs.income.amt.exemption.amount.HEAD_OF_HOUSEHOLD": {
            "2026-01-01.2026-12-31": 89925,
            "2027-01-01.2027-12-31": 91750,
            "2028-01-01.2028-12-31": 93525,
            "2029-01-01.2029-12-31": 95300,
            "2030-01-01.2030-12-31": 97150,
            "2031-01-01.2031-12-31": 99075,
            "2032-01-01.2032-12-31": 101050,
            "2033-01-01.2033-12-31": 103075,
            "2034-01-01.2034-12-31": 105150,
            "2035-01-01.2035-12-31": 107275,
        },
        "gov.irs.income.amt.exemption.phase_out.start.SEPARATE": {
            "2026-01-01.2026-12-31": 639300,
            "2027-01-01.2027-12-31": 652250,
            "2028-01-01.2028-12-31": 664825,
            "2029-01-01.2029-12-31": 677425,
            "2030-01-01.2030-12-31": 690725,
            "2031-01-01.2031-12-31": 704400,
            "2032-01-01.2032-12-31": 718425,
            "2033-01-01.2033-12-31": 732825,
            "2034-01-01.2034-12-31": 747575,
            "2035-01-01.2035-12-31": 762675,
        },
        "gov.irs.income.bracket.thresholds.3.HEAD_OF_HOUSEHOLD": {
            "2026-01-01.2026-12-31": 105475,
            "2027-01-01.2027-12-31": 107600,
            "2028-01-01.2028-12-31": 109700,
            "2029-01-01.2029-12-31": 111775,
            "2030-01-01.2030-12-31": 113950,
            "2031-01-01.2031-12-31": 116225,
            "2032-01-01.2032-12-31": 118525,
            "2033-01-01.2033-12-31": 120900,
            "2034-01-01.2034-12-31": 123350,
            "2035-01-01.2035-12-31": 125825,
        },
        "gov.irs.income.bracket.thresholds.4.HEAD_OF_HOUSEHOLD": {
            "2026-01-01.2026-12-31": 201350,
            "2027-01-01.2027-12-31": 205425,
            "2028-01-01.2028-12-31": 209400,
            "2029-01-01.2029-12-31": 213375,
            "2030-01-01.2030-12-31": 217550,
            "2031-01-01.2031-12-31": 221875,
            "2032-01-01.2032-12-31": 226275,
            "2033-01-01.2033-12-31": 230825,
            "2034-01-01.2034-12-31": 235475,
            "2035-01-01.2035-12-31": 240225,
        },
        "gov.irs.income.bracket.thresholds.5.HEAD_OF_HOUSEHOLD": {
            "2026-01-01.2026-12-31": 255700,
            "2027-01-01.2027-12-31": 260875,
            "2028-01-01.2028-12-31": 265925,
            "2029-01-01.2029-12-31": 270950,
            "2030-01-01.2030-12-31": 276275,
            "2031-01-01.2031-12-31": 281750,
            "2032-01-01.2032-12-31": 287375,
            "2033-01-01.2033-12-31": 293125,
            "2034-01-01.2034-12-31": 299025,
            "2035-01-01.2035-12-31": 305075,
        },
        "gov.irs.income.bracket.thresholds.6.HEAD_OF_HOUSEHOLD": {
            "2026-01-01.2026-12-31": 639300,
            "2027-01-01.2027-12-31": 652250,
            "2028-01-01.2028-12-31": 664825,
            "2029-01-01.2029-12-31": 677425,
            "2030-01-01.2030-12-31": 690725,
            "2031-01-01.2031-12-31": 704400,
            "2032-01-01.2032-12-31": 718425,
            "2033-01-01.2033-12-31": 732825,
            "2034-01-01.2034-12-31": 747575,
            "2035-01-01.2035-12-31": 762675,
        },
        "gov.irs.deductions.qbi.phase_out.start.SURVIVING_SPOUSE": {
            "2024-01-01.2024-12-31": 396450,
            "2025-01-01.2025-12-31": 400575,
            "2026-01-01.2026-12-31": 409800,
            "2027-01-01.2027-12-31": 418100,
            "2028-01-01.2028-12-31": 426175,
            "2029-01-01.2029-12-31": 434225,
            "2030-01-01.2030-12-31": 442775,
            "2031-01-01.2031-12-31": 451525,
            "2032-01-01.2032-12-31": 460525,
            "2033-01-01.2033-12-31": 469750,
            "2034-01-01.2034-12-31": 479200,
            "2035-01-01.2035-12-31": 488900,
        },
        "gov.irs.credits.ctc.phase_out.threshold.SURVIVING_SPOUSE": {
            "2026-01-01.2100-12-31": 400000
        },
        "gov.irs.deductions.qbi.phase_out.length.SURVIVING_SPOUSE": {
            "2026-01-01.2100-12-31": 100000
        },
        "gov.irs.deductions.qbi.phase_out.start.HEAD_OF_HOUSEHOLD": {
            "2024-01-01.2024-12-31": 198225,
            "2025-01-01.2025-12-31": 200275,
            "2026-01-01.2026-12-31": 204900,
            "2027-01-01.2027-12-31": 209050,
            "2028-01-01.2028-12-31": 213075,
            "2029-01-01.2029-12-31": 217125,
            "2030-01-01.2030-12-31": 221375,
            "2031-01-01.2031-12-31": 225775,
            "2032-01-01.2032-12-31": 230275,
            "2033-01-01.2033-12-31": 234875,
            "2034-01-01.2034-12-31": 239600,
            "2035-01-01.2035-12-31": 244450,
        },
        "gov.irs.credits.ctc.phase_out.threshold.HEAD_OF_HOUSEHOLD": {
            "2026-01-01.2100-12-31": 200000
        },
        "gov.irs.deductions.qbi.phase_out.length.HEAD_OF_HOUSEHOLD": {
            "2026-01-01.2100-12-31": 50000
        },
        "gov.irs.deductions.itemized.salt_and_real_estate.cap.JOINT": {
            "2026-01-01.2100-12-31": 10000
        },
        "gov.irs.deductions.itemized.salt_and_real_estate.cap.SINGLE": {
            "2026-01-01.2100-12-31": 10000
        },
        "gov.irs.deductions.itemized.salt_and_real_estate.cap.SEPARATE": {
            "2026-01-01.2100-12-31": 5000
        },
        "gov.irs.income.amt.exemption.phase_out.start.SURVIVING_SPOUSE": {
            "2026-01-01.2026-12-31": 1278575,
            "2027-01-01.2027-12-31": 1304475,
            "2028-01-01.2028-12-31": 1329675,
            "2029-01-01.2029-12-31": 1354850,
            "2030-01-01.2030-12-31": 1381475,
            "2031-01-01.2031-12-31": 1408825,
            "2032-01-01.2032-12-31": 1436875,
            "2033-01-01.2033-12-31": 1465650,
            "2034-01-01.2034-12-31": 1495150,
            "2035-01-01.2035-12-31": 1525375,
        },
        "gov.irs.deductions.itemized.limitation.applicable_amount.JOINT": {
            "2026-01-01.2100-12-31": np.inf
        },
        "gov.irs.deductions.itemized.limitation.itemized_deduction_rate": {
            "2026-01-01.2100-12-31": np.inf
        },
        "gov.irs.income.amt.exemption.phase_out.start.HEAD_OF_HOUSEHOLD": {
            "2026-01-01.2026-12-31": 639300,
            "2027-01-01.2027-12-31": 652250,
            "2028-01-01.2028-12-31": 664825,
            "2029-01-01.2029-12-31": 677425,
            "2030-01-01.2030-12-31": 690725,
            "2031-01-01.2031-12-31": 704400,
            "2032-01-01.2032-12-31": 718425,
            "2033-01-01.2033-12-31": 732825,
            "2034-01-01.2034-12-31": 747575,
            "2035-01-01.2035-12-31": 762675,
        },
        "gov.irs.deductions.itemized.limitation.applicable_amount.SINGLE": {
            "2026-01-01.2100-12-31": np.inf
        },
        "gov.irs.deductions.itemized.limitation.applicable_amount.SEPARATE": {
            "2026-01-01.2100-12-31": np.inf
        },
        "gov.irs.deductions.itemized.salt_and_real_estate.cap.SURVIVING_SPOUSE": {
            "2026-01-01.2100-12-31": 10000
        },
        "gov.irs.deductions.itemized.salt_and_real_estate.cap.HEAD_OF_HOUSEHOLD": {
            "2026-01-01.2100-12-31": 10000
        },
        "gov.irs.deductions.itemized.limitation.applicable_amount.SURVIVING_SPOUSE": {
            "2026-01-01.2100-12-31": np.inf
        },
        "gov.irs.deductions.itemized.limitation.applicable_amount.HEAD_OF_HOUSEHOLD": {
            "2026-01-01.2100-12-31": np.inf
        },
        "gov.simulation.branch_to_determine_itemization": {
            "2026-01-01.2100-12-31": True
        },
    },
    country_id="us",
)


In [10]:

current_policy_50k = Reform.from_dict(
    {
        "gov.irs.income.bracket.rates.2": {"2026-01-01.2100-12-31": 0.12},
        "gov.irs.income.bracket.rates.3": {"2026-01-01.2100-12-31": 0.22},
        "gov.irs.income.bracket.rates.4": {"2026-01-01.2100-12-31": 0.24},
        "gov.irs.income.bracket.rates.5": {"2026-01-01.2100-12-31": 0.32},
        "gov.irs.income.bracket.rates.7": {"2026-01-01.2100-12-31": 0.37},
        "gov.irs.deductions.qbi.max.rate": {"2026-01-01.2100-12-31": 0.2},
        "gov.irs.income.exemption.amount": {"2026-01-01.2100-12-31": 0},
        "gov.irs.deductions.qbi.max.w2_wages.rate": {"2026-01-01.2100-12-31": 0.5},
        "gov.irs.deductions.standard.amount.JOINT": {
            "2026-01-01.2026-12-31": 30600,
            "2027-01-01.2027-12-31": 31225,
            "2028-01-01.2028-12-31": 31825,
            "2029-01-01.2029-12-31": 32425,
            "2030-01-01.2030-12-31": 33050,
            "2031-01-01.2031-12-31": 33725,
            "2032-01-01.2032-12-31": 34400,
            "2033-01-01.2033-12-31": 35075,
            "2034-01-01.2034-12-31": 35775,
            "2035-01-01.2035-12-31": 36500,
        },
        "gov.irs.credits.ctc.amount.base[0].amount": {"2026-01-01.2100-12-31": 2000},
        "gov.irs.deductions.standard.amount.SINGLE": {
            "2026-01-01.2026-12-31": 15300,
            "2027-01-01.2027-12-31": 15600,
            "2028-01-01.2028-12-31": 15900,
            "2029-01-01.2029-12-31": 16225,
            "2030-01-01.2030-12-31": 16525,
            "2031-01-01.2031-12-31": 16850,
            "2032-01-01.2032-12-31": 17200,
            "2033-01-01.2033-12-31": 17550,
            "2034-01-01.2034-12-31": 17900,
            "2035-01-01.2035-12-31": 18250,
        },
        "gov.irs.income.amt.exemption.amount.JOINT": {
            "2026-01-01.2026-12-31": 139850,
            "2027-01-01.2027-12-31": 142675,
            "2028-01-01.2028-12-31": 145425,
            "2029-01-01.2029-12-31": 148200,
            "2030-01-01.2030-12-31": 151100,
            "2031-01-01.2031-12-31": 154100,
            "2032-01-01.2032-12-31": 157150,
            "2033-01-01.2033-12-31": 160300,
            "2034-01-01.2034-12-31": 163525,
            "2035-01-01.2035-12-31": 166850,
        },
        "gov.irs.income.bracket.thresholds.3.JOINT": {
            "2026-01-01.2026-12-31": 210950,
            "2027-01-01.2027-12-31": 215225,
            "2028-01-01.2028-12-31": 219375,
            "2029-01-01.2029-12-31": 223525,
            "2030-01-01.2030-12-31": 227925,
            "2031-01-01.2031-12-31": 232425,
            "2032-01-01.2032-12-31": 237075,
            "2033-01-01.2033-12-31": 241825,
            "2034-01-01.2034-12-31": 246675,
            "2035-01-01.2035-12-31": 251675,
        },
        "gov.irs.income.bracket.thresholds.4.JOINT": {
            "2026-01-01.2026-12-31": 402725,
            "2027-01-01.2027-12-31": 410875,
            "2028-01-01.2028-12-31": 418800,
            "2029-01-01.2029-12-31": 426725,
            "2030-01-01.2030-12-31": 435125,
            "2031-01-01.2031-12-31": 443725,
            "2032-01-01.2032-12-31": 452575,
            "2033-01-01.2033-12-31": 461650,
            "2034-01-01.2034-12-31": 470925,
            "2035-01-01.2035-12-31": 480450,
        },
        "gov.irs.income.bracket.thresholds.5.JOINT": {
            "2026-01-01.2026-12-31": 511400,
            "2027-01-01.2027-12-31": 521775,
            "2028-01-01.2028-12-31": 531850,
            "2029-01-01.2029-12-31": 541925,
            "2030-01-01.2030-12-31": 552575,
            "2031-01-01.2031-12-31": 563500,
            "2032-01-01.2032-12-31": 574725,
            "2033-01-01.2033-12-31": 586250,
            "2034-01-01.2034-12-31": 598050,
            "2035-01-01.2035-12-31": 610125,
        },
        "gov.irs.income.bracket.thresholds.6.JOINT": {
            "2026-01-01.2026-12-31": 767125,
            "2027-01-01.2027-12-31": 782650,
            "2028-01-01.2028-12-31": 797775,
            "2029-01-01.2029-12-31": 812875,
            "2030-01-01.2030-12-31": 828850,
            "2031-01-01.2031-12-31": 845250,
            "2032-01-01.2032-12-31": 862100,
            "2033-01-01.2033-12-31": 879350,
            "2034-01-01.2034-12-31": 897050,
            "2035-01-01.2035-12-31": 915200,
        },
        "gov.irs.credits.ctc.amount.adult_dependent": {"2026-01-01.2100-12-31": 500},
        "gov.irs.income.amt.exemption.amount.SINGLE": {
            "2026-01-01.2026-12-31": 89925,
            "2027-01-01.2027-12-31": 91750,
            "2028-01-01.2028-12-31": 93525,
            "2029-01-01.2029-12-31": 95300,
            "2030-01-01.2030-12-31": 97150,
            "2031-01-01.2031-12-31": 99075,
            "2032-01-01.2032-12-31": 101050,
            "2033-01-01.2033-12-31": 103075,
            "2034-01-01.2034-12-31": 105150,
            "2035-01-01.2035-12-31": 107275,
        },
        "gov.irs.income.bracket.thresholds.3.SINGLE": {
            "2026-01-01.2026-12-31": 105475,
            "2027-01-01.2027-12-31": 107600,
            "2028-01-01.2028-12-31": 109700,
            "2029-01-01.2029-12-31": 111775,
            "2030-01-01.2030-12-31": 113950,
            "2031-01-01.2031-12-31": 116225,
            "2032-01-01.2032-12-31": 118525,
            "2033-01-01.2033-12-31": 120900,
            "2034-01-01.2034-12-31": 123350,
            "2035-01-01.2035-12-31": 125825,
        },
        "gov.irs.income.bracket.thresholds.4.SINGLE": {
            "2026-01-01.2026-12-31": 201350,
            "2027-01-01.2027-12-31": 205425,
            "2028-01-01.2028-12-31": 209400,
            "2029-01-01.2029-12-31": 213375,
            "2030-01-01.2030-12-31": 217550,
            "2031-01-01.2031-12-31": 221875,
            "2032-01-01.2032-12-31": 226275,
            "2033-01-01.2033-12-31": 230825,
            "2034-01-01.2034-12-31": 235475,
            "2035-01-01.2035-12-31": 240225,
        },
        "gov.irs.income.bracket.thresholds.5.SINGLE": {
            "2026-01-01.2026-12-31": 255700,
            "2027-01-01.2027-12-31": 260875,
            "2028-01-01.2028-12-31": 265925,
            "2029-01-01.2029-12-31": 270950,
            "2030-01-01.2030-12-31": 276275,
            "2031-01-01.2031-12-31": 281750,
            "2032-01-01.2032-12-31": 287375,
            "2033-01-01.2033-12-31": 293125,
            "2034-01-01.2034-12-31": 299025,
            "2035-01-01.2035-12-31": 305075,
        },
        "gov.irs.income.bracket.thresholds.6.SINGLE": {
            "2026-01-01.2026-12-31": 639300,
            "2027-01-01.2027-12-31": 652250,
            "2028-01-01.2028-12-31": 664825,
            "2029-01-01.2029-12-31": 677425,
            "2030-01-01.2030-12-31": 690725,
            "2031-01-01.2031-12-31": 704400,
            "2032-01-01.2032-12-31": 718425,
            "2033-01-01.2033-12-31": 732825,
            "2034-01-01.2034-12-31": 747575,
            "2035-01-01.2035-12-31": 762675,
        },
        "gov.irs.deductions.itemized.casualty.active": {"2026-01-01.2100-12-31": False},
        "gov.irs.deductions.standard.amount.SEPARATE": {
            "2026-01-01.2026-12-31": 15300,
            "2027-01-01.2027-12-31": 15600,
            "2028-01-01.2028-12-31": 15900,
            "2029-01-01.2029-12-31": 16225,
            "2030-01-01.2030-12-31": 16525,
            "2031-01-01.2031-12-31": 16850,
            "2032-01-01.2032-12-31": 17200,
            "2033-01-01.2033-12-31": 17550,
            "2034-01-01.2034-12-31": 17900,
            "2035-01-01.2035-12-31": 18250,
        },
        "gov.irs.deductions.qbi.max.w2_wages.alt_rate": {"2026-01-01.2100-12-31": 0.25},
        "gov.irs.deductions.qbi.phase_out.start.JOINT": {
            "2024-01-01.2024-12-31": 396450,
            "2025-01-01.2025-12-31": 400575,
            "2026-01-01.2026-12-31": 409800,
            "2027-01-01.2027-12-31": 418100,
            "2028-01-01.2028-12-31": 426175,
            "2029-01-01.2029-12-31": 434225,
            "2030-01-01.2030-12-31": 442775,
            "2031-01-01.2031-12-31": 451525,
            "2032-01-01.2032-12-31": 460525,
            "2033-01-01.2033-12-31": 469750,
            "2034-01-01.2034-12-31": 479200,
            "2035-01-01.2035-12-31": 488900,
        },
        "gov.irs.income.amt.exemption.amount.SEPARATE": {
            "2026-01-01.2026-12-31": 69925,
            "2027-01-01.2027-12-31": 71350,
            "2028-01-01.2028-12-31": 72725,
            "2029-01-01.2029-12-31": 74100,
            "2030-01-01.2030-12-31": 75550,
            "2031-01-01.2031-12-31": 77050,
            "2032-01-01.2032-12-31": 78575,
            "2033-01-01.2033-12-31": 80150,
            "2034-01-01.2034-12-31": 81775,
            "2035-01-01.2035-12-31": 83425,
        },
        "gov.irs.income.bracket.thresholds.3.SEPARATE": {
            "2026-01-01.2026-12-31": 105475,
            "2027-01-01.2027-12-31": 107600,
            "2028-01-01.2028-12-31": 109700,
            "2029-01-01.2029-12-31": 111775,
            "2030-01-01.2030-12-31": 113950,
            "2031-01-01.2031-12-31": 116225,
            "2032-01-01.2032-12-31": 118525,
            "2033-01-01.2033-12-31": 120900,
            "2034-01-01.2034-12-31": 123350,
            "2035-01-01.2035-12-31": 125825,
        },
        "gov.irs.income.bracket.thresholds.4.SEPARATE": {
            "2026-01-01.2026-12-31": 201350,
            "2027-01-01.2027-12-31": 205425,
            "2028-01-01.2028-12-31": 209400,
            "2029-01-01.2029-12-31": 213375,
            "2030-01-01.2030-12-31": 217550,
            "2031-01-01.2031-12-31": 221875,
            "2032-01-01.2032-12-31": 226275,
            "2033-01-01.2033-12-31": 230825,
            "2034-01-01.2034-12-31": 235475,
            "2035-01-01.2035-12-31": 240225,
        },
        "gov.irs.income.bracket.thresholds.5.SEPARATE": {
            "2026-01-01.2026-12-31": 255700,
            "2027-01-01.2027-12-31": 260875,
            "2028-01-01.2028-12-31": 265925,
            "2029-01-01.2029-12-31": 270950,
            "2030-01-01.2030-12-31": 276275,
            "2031-01-01.2031-12-31": 281750,
            "2032-01-01.2032-12-31": 287375,
            "2033-01-01.2033-12-31": 293125,
            "2034-01-01.2034-12-31": 299025,
            "2035-01-01.2035-12-31": 305075,
        },
        "gov.irs.income.bracket.thresholds.6.SEPARATE": {
            "2026-01-01.2026-12-31": 383550,
            "2027-01-01.2027-12-31": 391325,
            "2028-01-01.2028-12-31": 398875,
            "2029-01-01.2029-12-31": 406450,
            "2030-01-01.2030-12-31": 414425,
            "2031-01-01.2031-12-31": 422625,
            "2032-01-01.2032-12-31": 431050,
            "2033-01-01.2033-12-31": 439675,
            "2034-01-01.2034-12-31": 448525,
            "2035-01-01.2035-12-31": 457600,
        },
        "gov.irs.credits.ctc.phase_out.threshold.JOINT": {
            "2026-01-01.2100-12-31": 400000
        },
        "gov.irs.credits.ctc.refundable.individual_max": {
            "2026-01-01.2026-12-31": 1800,
            "2027-01-01.2027-12-31": 1800,
            "2028-01-01.2028-12-31": 1800,
            "2029-01-01.2029-12-31": 1900,
            "2030-01-01.2030-12-31": 1900,
            "2031-01-01.2031-12-31": 1900,
            "2032-01-01.2032-12-31": 2000,
            "2033-01-01.2033-12-31": 2000,
            "2034-01-01.2034-12-31": 2000,
            "2035-01-01.2035-12-31": 2000,
        },
        "gov.irs.deductions.qbi.phase_out.length.JOINT": {
            "2026-01-01.2100-12-31": 100000
        },
        "gov.irs.deductions.qbi.phase_out.start.SINGLE": {
            "2024-01-01.2024-12-31": 198225,
            "2025-01-01.2025-12-31": 200275,
            "2026-01-01.2026-12-31": 204900,
            "2027-01-01.2027-12-31": 209050,
            "2028-01-01.2028-12-31": 213075,
            "2029-01-01.2029-12-31": 217125,
            "2030-01-01.2030-12-31": 221375,
            "2031-01-01.2031-12-31": 225775,
            "2032-01-01.2032-12-31": 230275,
            "2033-01-01.2033-12-31": 234875,
            "2034-01-01.2034-12-31": 239600,
            "2035-01-01.2035-12-31": 244450,
        },
        "gov.irs.credits.ctc.phase_out.threshold.SINGLE": {
            "2026-01-01.2100-12-31": 200000
        },
        "gov.irs.deductions.qbi.phase_out.length.SINGLE": {
            "2026-01-01.2100-12-31": 50000
        },
        "gov.irs.deductions.itemized.charity.ceiling.all": {
            "2026-01-01.2100-12-31": 0.6
        },
        "gov.irs.deductions.itemized.limitation.agi_rate": {
            "2026-01-01.2100-12-31": np.inf
        },
        "gov.irs.deductions.qbi.phase_out.start.SEPARATE": {
            "2024-01-01.2024-12-31": 198225,
            "2025-01-01.2025-12-31": 200275,
            "2026-01-01.2026-12-31": 204900,
            "2027-01-01.2027-12-31": 209050,
            "2028-01-01.2028-12-31": 213075,
            "2029-01-01.2029-12-31": 217125,
            "2030-01-01.2030-12-31": 221375,
            "2031-01-01.2031-12-31": 225775,
            "2032-01-01.2032-12-31": 230275,
            "2033-01-01.2033-12-31": 234875,
            "2034-01-01.2034-12-31": 239600,
            "2035-01-01.2035-12-31": 244450,
        },
        "gov.irs.credits.ctc.phase_out.threshold.SEPARATE": {
            "2026-01-01.2100-12-31": 200000
        },
        "gov.irs.deductions.qbi.phase_out.length.SEPARATE": {
            "2026-01-01.2100-12-31": 50000
        },
        "gov.irs.credits.ctc.refundable.phase_in.threshold": {
            "2026-01-01.2100-12-31": 2500
        },
        "gov.irs.deductions.qbi.max.business_property.rate": {
            "2026-01-01.2100-12-31": 0.025
        },
        "gov.irs.income.amt.exemption.phase_out.start.JOINT": {
            "2026-01-01.2026-12-31": 1278575,
            "2027-01-01.2027-12-31": 1304475,
            "2028-01-01.2028-12-31": 1329675,
            "2029-01-01.2029-12-31": 1354850,
            "2030-01-01.2030-12-31": 1381475,
            "2031-01-01.2031-12-31": 1408825,
            "2032-01-01.2032-12-31": 1436875,
            "2033-01-01.2033-12-31": 1465650,
            "2034-01-01.2034-12-31": 1495150,
            "2035-01-01.2035-12-31": 1525375,
        },
        "gov.irs.deductions.standard.amount.SURVIVING_SPOUSE": {
            "2026-01-01.2026-12-31": 30600,
            "2027-01-01.2027-12-31": 31225,
            "2028-01-01.2028-12-31": 31825,
            "2029-01-01.2029-12-31": 32425,
            "2030-01-01.2030-12-31": 33050,
            "2031-01-01.2031-12-31": 33725,
            "2032-01-01.2032-12-31": 34400,
            "2033-01-01.2033-12-31": 35075,
            "2034-01-01.2034-12-31": 35775,
            "2035-01-01.2035-12-31": 36500,
        },
        "gov.irs.income.amt.exemption.phase_out.start.SINGLE": {
            "2026-01-01.2026-12-31": 639300,
            "2027-01-01.2027-12-31": 652250,
            "2028-01-01.2028-12-31": 664825,
            "2029-01-01.2029-12-31": 677425,
            "2030-01-01.2030-12-31": 690725,
            "2031-01-01.2031-12-31": 704400,
            "2032-01-01.2032-12-31": 718425,
            "2033-01-01.2033-12-31": 732825,
            "2034-01-01.2034-12-31": 747575,
            "2035-01-01.2035-12-31": 762675,
        },
        "gov.irs.deductions.standard.amount.HEAD_OF_HOUSEHOLD": {
            "2026-01-01.2026-12-31": 22950,
            "2027-01-01.2027-12-31": 23425,
            "2028-01-01.2028-12-31": 23875,
            "2029-01-01.2029-12-31": 24325,
            "2030-01-01.2030-12-31": 24800,
            "2031-01-01.2031-12-31": 25300,
            "2032-01-01.2032-12-31": 25800,
            "2033-01-01.2033-12-31": 26300,
            "2034-01-01.2034-12-31": 26825,
            "2035-01-01.2035-12-31": 27375,
        },
        "gov.irs.income.amt.exemption.amount.SURVIVING_SPOUSE": {
            "2026-01-01.2026-12-31": 139850,
            "2027-01-01.2027-12-31": 142675,
            "2028-01-01.2028-12-31": 145425,
            "2029-01-01.2029-12-31": 148200,
            "2030-01-01.2030-12-31": 151100,
            "2031-01-01.2031-12-31": 154100,
            "2032-01-01.2032-12-31": 157150,
            "2033-01-01.2033-12-31": 160300,
            "2034-01-01.2034-12-31": 163525,
            "2035-01-01.2035-12-31": 166850,
        },
        "gov.irs.income.bracket.thresholds.3.SURVIVING_SPOUSE": {
            "2026-01-01.2026-12-31": 210950,
            "2027-01-01.2027-12-31": 215225,
            "2028-01-01.2028-12-31": 219375,
            "2029-01-01.2029-12-31": 223525,
            "2030-01-01.2030-12-31": 227925,
            "2031-01-01.2031-12-31": 232425,
            "2032-01-01.2032-12-31": 237075,
            "2033-01-01.2033-12-31": 241825,
            "2034-01-01.2034-12-31": 246675,
            "2035-01-01.2035-12-31": 251675,
        },
        "gov.irs.income.bracket.thresholds.4.SURVIVING_SPOUSE": {
            "2026-01-01.2026-12-31": 402725,
            "2027-01-01.2027-12-31": 410875,
            "2028-01-01.2028-12-31": 418800,
            "2029-01-01.2029-12-31": 426725,
            "2030-01-01.2030-12-31": 435125,
            "2031-01-01.2031-12-31": 443725,
            "2032-01-01.2032-12-31": 452575,
            "2033-01-01.2033-12-31": 461650,
            "2034-01-01.2034-12-31": 470925,
            "2035-01-01.2035-12-31": 480450,
        },
        "gov.irs.income.bracket.thresholds.5.SURVIVING_SPOUSE": {
            "2026-01-01.2026-12-31": 511400,
            "2027-01-01.2027-12-31": 521775,
            "2028-01-01.2028-12-31": 531850,
            "2029-01-01.2029-12-31": 541925,
            "2030-01-01.2030-12-31": 552575,
            "2031-01-01.2031-12-31": 563500,
            "2032-01-01.2032-12-31": 574725,
            "2033-01-01.2033-12-31": 586250,
            "2034-01-01.2034-12-31": 598050,
            "2035-01-01.2035-12-31": 610125,
        },
        "gov.irs.income.bracket.thresholds.6.SURVIVING_SPOUSE": {
            "2026-01-01.2026-12-31": 767125,
            "2027-01-01.2027-12-31": 782650,
            "2028-01-01.2028-12-31": 797775,
            "2029-01-01.2029-12-31": 812875,
            "2030-01-01.2030-12-31": 828850,
            "2031-01-01.2031-12-31": 845250,
            "2032-01-01.2032-12-31": 862100,
            "2033-01-01.2033-12-31": 879350,
            "2034-01-01.2034-12-31": 897050,
            "2035-01-01.2035-12-31": 915200,
        },
        "gov.irs.income.amt.exemption.amount.HEAD_OF_HOUSEHOLD": {
            "2026-01-01.2026-12-31": 89925,
            "2027-01-01.2027-12-31": 91750,
            "2028-01-01.2028-12-31": 93525,
            "2029-01-01.2029-12-31": 95300,
            "2030-01-01.2030-12-31": 97150,
            "2031-01-01.2031-12-31": 99075,
            "2032-01-01.2032-12-31": 101050,
            "2033-01-01.2033-12-31": 103075,
            "2034-01-01.2034-12-31": 105150,
            "2035-01-01.2035-12-31": 107275,
        },
        "gov.irs.income.amt.exemption.phase_out.start.SEPARATE": {
            "2026-01-01.2026-12-31": 639300,
            "2027-01-01.2027-12-31": 652250,
            "2028-01-01.2028-12-31": 664825,
            "2029-01-01.2029-12-31": 677425,
            "2030-01-01.2030-12-31": 690725,
            "2031-01-01.2031-12-31": 704400,
            "2032-01-01.2032-12-31": 718425,
            "2033-01-01.2033-12-31": 732825,
            "2034-01-01.2034-12-31": 747575,
            "2035-01-01.2035-12-31": 762675,
        },
        "gov.irs.income.bracket.thresholds.3.HEAD_OF_HOUSEHOLD": {
            "2026-01-01.2026-12-31": 105475,
            "2027-01-01.2027-12-31": 107600,
            "2028-01-01.2028-12-31": 109700,
            "2029-01-01.2029-12-31": 111775,
            "2030-01-01.2030-12-31": 113950,
            "2031-01-01.2031-12-31": 116225,
            "2032-01-01.2032-12-31": 118525,
            "2033-01-01.2033-12-31": 120900,
            "2034-01-01.2034-12-31": 123350,
            "2035-01-01.2035-12-31": 125825,
        },
        "gov.irs.income.bracket.thresholds.4.HEAD_OF_HOUSEHOLD": {
            "2026-01-01.2026-12-31": 201350,
            "2027-01-01.2027-12-31": 205425,
            "2028-01-01.2028-12-31": 209400,
            "2029-01-01.2029-12-31": 213375,
            "2030-01-01.2030-12-31": 217550,
            "2031-01-01.2031-12-31": 221875,
            "2032-01-01.2032-12-31": 226275,
            "2033-01-01.2033-12-31": 230825,
            "2034-01-01.2034-12-31": 235475,
            "2035-01-01.2035-12-31": 240225,
        },
        "gov.irs.income.bracket.thresholds.5.HEAD_OF_HOUSEHOLD": {
            "2026-01-01.2026-12-31": 255700,
            "2027-01-01.2027-12-31": 260875,
            "2028-01-01.2028-12-31": 265925,
            "2029-01-01.2029-12-31": 270950,
            "2030-01-01.2030-12-31": 276275,
            "2031-01-01.2031-12-31": 281750,
            "2032-01-01.2032-12-31": 287375,
            "2033-01-01.2033-12-31": 293125,
            "2034-01-01.2034-12-31": 299025,
            "2035-01-01.2035-12-31": 305075,
        },
        "gov.irs.income.bracket.thresholds.6.HEAD_OF_HOUSEHOLD": {
            "2026-01-01.2026-12-31": 639300,
            "2027-01-01.2027-12-31": 652250,
            "2028-01-01.2028-12-31": 664825,
            "2029-01-01.2029-12-31": 677425,
            "2030-01-01.2030-12-31": 690725,
            "2031-01-01.2031-12-31": 704400,
            "2032-01-01.2032-12-31": 718425,
            "2033-01-01.2033-12-31": 732825,
            "2034-01-01.2034-12-31": 747575,
            "2035-01-01.2035-12-31": 762675,
        },
        "gov.irs.deductions.qbi.phase_out.start.SURVIVING_SPOUSE": {
            "2024-01-01.2024-12-31": 396450,
            "2025-01-01.2025-12-31": 400575,
            "2026-01-01.2026-12-31": 409800,
            "2027-01-01.2027-12-31": 418100,
            "2028-01-01.2028-12-31": 426175,
            "2029-01-01.2029-12-31": 434225,
            "2030-01-01.2030-12-31": 442775,
            "2031-01-01.2031-12-31": 451525,
            "2032-01-01.2032-12-31": 460525,
            "2033-01-01.2033-12-31": 469750,
            "2034-01-01.2034-12-31": 479200,
            "2035-01-01.2035-12-31": 488900,
        },
        "gov.irs.credits.ctc.phase_out.threshold.SURVIVING_SPOUSE": {
            "2026-01-01.2100-12-31": 400000
        },
        "gov.irs.deductions.qbi.phase_out.length.SURVIVING_SPOUSE": {
            "2026-01-01.2100-12-31": 100000
        },
        "gov.irs.deductions.qbi.phase_out.start.HEAD_OF_HOUSEHOLD": {
            "2024-01-01.2024-12-31": 198225,
            "2025-01-01.2025-12-31": 200275,
            "2026-01-01.2026-12-31": 204900,
            "2027-01-01.2027-12-31": 209050,
            "2028-01-01.2028-12-31": 213075,
            "2029-01-01.2029-12-31": 217125,
            "2030-01-01.2030-12-31": 221375,
            "2031-01-01.2031-12-31": 225775,
            "2032-01-01.2032-12-31": 230275,
            "2033-01-01.2033-12-31": 234875,
            "2034-01-01.2034-12-31": 239600,
            "2035-01-01.2035-12-31": 244450,
        },
        "gov.irs.credits.ctc.phase_out.threshold.HEAD_OF_HOUSEHOLD": {
            "2026-01-01.2100-12-31": 200000
        },
        "gov.irs.deductions.qbi.phase_out.length.HEAD_OF_HOUSEHOLD": {
            "2026-01-01.2100-12-31": 50000
        },
        "gov.irs.deductions.itemized.salt_and_real_estate.cap.JOINT": {
            "2026-01-01.2100-12-31": 50000
        },
        "gov.irs.deductions.itemized.salt_and_real_estate.cap.SINGLE": {
            "2026-01-01.2100-12-31": 25000
        },
        "gov.irs.deductions.itemized.salt_and_real_estate.cap.SEPARATE": {
            "2026-01-01.2100-12-31": 25000
        },
        "gov.irs.income.amt.exemption.phase_out.start.SURVIVING_SPOUSE": {
            "2026-01-01.2026-12-31": 1278575,
            "2027-01-01.2027-12-31": 1304475,
            "2028-01-01.2028-12-31": 1329675,
            "2029-01-01.2029-12-31": 1354850,
            "2030-01-01.2030-12-31": 1381475,
            "2031-01-01.2031-12-31": 1408825,
            "2032-01-01.2032-12-31": 1436875,
            "2033-01-01.2033-12-31": 1465650,
            "2034-01-01.2034-12-31": 1495150,
            "2035-01-01.2035-12-31": 1525375,
        },
        "gov.irs.deductions.itemized.limitation.applicable_amount.JOINT": {
            "2026-01-01.2100-12-31": np.inf
        },
        "gov.irs.deductions.itemized.limitation.itemized_deduction_rate": {
            "2026-01-01.2100-12-31": np.inf
        },
        "gov.irs.income.amt.exemption.phase_out.start.HEAD_OF_HOUSEHOLD": {
            "2026-01-01.2026-12-31": 639300,
            "2027-01-01.2027-12-31": 652250,
            "2028-01-01.2028-12-31": 664825,
            "2029-01-01.2029-12-31": 677425,
            "2030-01-01.2030-12-31": 690725,
            "2031-01-01.2031-12-31": 704400,
            "2032-01-01.2032-12-31": 718425,
            "2033-01-01.2033-12-31": 732825,
            "2034-01-01.2034-12-31": 747575,
            "2035-01-01.2035-12-31": 762675,
        },
        "gov.irs.deductions.itemized.limitation.applicable_amount.SINGLE": {
            "2026-01-01.2100-12-31": np.inf
        },
        "gov.irs.deductions.itemized.limitation.applicable_amount.SEPARATE": {
            "2026-01-01.2100-12-31": np.inf
        },
        "gov.irs.deductions.itemized.salt_and_real_estate.cap.SURVIVING_SPOUSE": {
            "2026-01-01.2100-12-31": 50000
        },
        "gov.irs.deductions.itemized.salt_and_real_estate.cap.HEAD_OF_HOUSEHOLD": {
            "2026-01-01.2100-12-31": 25000
        },
        "gov.irs.deductions.itemized.limitation.applicable_amount.SURVIVING_SPOUSE": {
            "2026-01-01.2100-12-31": np.inf
        },
        "gov.irs.deductions.itemized.limitation.applicable_amount.HEAD_OF_HOUSEHOLD": {
            "2026-01-01.2100-12-31": np.inf
        },
        "gov.simulation.branch_to_determine_itemization": {
            "2026-01-01.2100-12-31": True
        },
    },
    country_id="us",
)


In [12]:

baseline_brachning_reform = Reform.from_dict(
    {
        "gov.simulation.branch_to_determine_itemization": {"2026-01-01.2100-12-31": True},
    },
    country_id="us",
)


## Setup Household Scenarios

Each household is married filing jointly across four states (NY, NJ, CA, PA) with the following income and property tax levels:
1. $250k income ($11,250 property tax)
2. $500k income ($22,500 property tax)
3. $750k income ($33,750 property tax)
4. $1M income ($45,000 property tax)

In [13]:
# Define the states and income/tax levels
states = ["NY", "NJ", "CA", "PA"]
income_levels = [250000, 500000, 750000, 1000000]
property_taxes = [11250, 22500, 33750, 45000]

In [28]:
# Function to calculate net income and other metrics for a given scenario
def calculate_metrics(state, income, property_tax, reform):
    # Create the situation dictionary with this state, income, and property tax
    situation = {
        "people": {
            "you": {
                "age": {2026: 40},
                "employment_income": {2026: income},
                "real_estate_taxes": {2026: property_tax},
            },
            "your partner": {"age": {2026: 40}},
        },
        "families": {"your family": {"members": ["you", "your partner"]}},
        "tax_units": {"your tax unit": {"members": ["you", "your partner"]}},
        "spm_units": {"your household": {"members": ["you", "your partner"]}},
        "households": {
            "your household": {
                "members": ["you", "your partner"],
                "state_name": {2026: state},
            }
        },
    }
    
    # Run the simulation
    simulation = Simulation(situation=situation, reform=reform)
    
    # Calculate and return metrics
    return {
        "net_income": simulation.calculate("household_net_income", 2026)[0],
        "regular_tax": simulation.calculate("regular_tax_before_credits", 2026)[0],
        "amt": simulation.calculate("amt_base_tax", 2026)[0],
        "salt_deduction": simulation.calculate("salt_deduction", 2026)[0],
        "federal_tax": simulation.calculate("income_tax", 2026)[0]
    }

In [29]:
# Create lists to store results
results_data = []

# Calculate results for all scenarios
for state in states:
    for i, income in enumerate(income_levels):
        property_tax = property_taxes[i]
        
        # Run the simulations for each policy
        current_law_results = calculate_metrics(state, income, property_tax, baseline_brachning_reform)
        current_policy_results = calculate_metrics(state, income, property_tax, current_policy)
        current_policy_50k_results = calculate_metrics(state, income, property_tax, current_policy_50k)
        
        # Add results to our data list
        results_data.append({
            "state": state,
            "income": income,
            "property_tax": property_tax,
            "current_law_net_income": current_law_results["net_income"],
            "current_policy_net_income": current_policy_results["net_income"],
            "current_policy_50k_net_income": current_policy_50k_results["net_income"],
            "current_law_regular_tax": current_law_results["regular_tax"],
            "current_law_amt": current_law_results["amt"],
            "current_law_salt_deduction": current_law_results["salt_deduction"],
            "current_policy_regular_tax": current_policy_results["regular_tax"],
            "current_policy_amt": current_policy_results["amt"],
            "current_policy_salt_deduction": current_policy_results["salt_deduction"],
            "current_policy_50k_regular_tax": current_policy_50k_results["regular_tax"],
            "current_policy_50k_amt": current_policy_50k_results["amt"],
            "current_policy_50k_salt_deduction": current_policy_50k_results["salt_deduction"]
        })

# Convert to DataFrame
results_df = pd.DataFrame(results_data)
results_df

state   income  property_tax  current_law_net_income  \
0     NY   250000         11250             $177,939.05   
1     NY   500000         22500             $321,527.69   
2     NY   750000         33750             $468,910.31   
3     NY  1000000         45000             $620,758.88   
4     NJ   250000         11250             $180,813.34   
5     NJ   500000         22500             $327,511.41   
6     NJ   750000         33750             $469,265.41   
7     NJ  1000000         45000             $618,580.12   
8     CA   250000         11250             $178,649.25   
9     CA   500000         22500             $317,125.12   
10    CA   750000         33750             $457,086.12   
11    CA  1000000         45000             $604,368.94   
12    PA   250000         11250             $182,460.00   
13    PA   500000         22500             $338,786.00   
14    PA   750000         33750             $494,848.00   
15    PA  1000000         45000             $641,574.19   

    current_policy_net_income  current_policy_50k_net_income  \
0                 $182,715.25                    $182,715.25   
1                 $342,834.69                    $349,042.69   
2                 $484,365.31                    $491,155.31   
3                 $620,590.44                    $627,768.44   
4                 $185,713.53                    $185,713.53   
5                 $348,818.41                    $355,026.41   
6                 $484,720.41                    $491,510.41   
7                 $614,874.88                    $622,052.88   
8                 $182,034.25                    $182,034.25   
9                 $338,432.12                    $344,640.12   
10                $472,541.12                    $479,331.12   
11                $598,278.44                    $605,456.44   
12                $189,057.00                    $189,057.00   
13                $360,093.00                    $362,413.00   
14                $510,303.00                    $517,093.00   
15                $655,207.50                    $662,385.50   

    current_law_regular_tax  current_law_amt  current_law_salt_deduction  \
0                $42,867.20       $39,104.00                  $25,427.85   
1               $114,130.88      $124,732.00                  $53,802.85   
2               $193,278.56      $205,120.00                  $82,177.85   
3               $281,042.06      $275,120.00                 $110,552.85   
4                $42,991.19       $39,104.00                  $24,985.05   
5               $114,672.99      $124,732.00                  $52,160.05   
6               $191,840.61      $205,120.00                  $85,809.05   
7               $277,505.31      $275,120.00                 $119,484.05   
8                $41,476.01       $39,104.00                  $30,396.41   
9               $109,923.93      $124,732.00                  $66,551.16   
10              $183,824.75      $205,120.00                 $106,051.16   
11              $266,209.09      $275,120.00                 $148,009.89   
12               $44,688.00       $39,104.00                  $18,925.00   
13              $119,395.31      $124,732.00                  $37,850.00   
14              $203,338.09      $205,120.00                  $56,775.00   
15              $294,843.81      $275,120.00                  $75,700.00   

    current_policy_regular_tax  current_policy_amt  \
0                   $38,091.00          $28,639.00   
1                  $103,425.00          $95,962.00   
2                  $189,665.00         $165,962.00   
3                  $281,210.50         $235,962.00   
4                   $38,091.00          $28,639.00   
5                  $103,425.00          $95,962.00   
6                  $189,665.00         $165,962.00   
7                  $281,210.50         $235,962.00   
8                   $38,091.00          $28,639.00   
9                  $103,425.00          $95,962.00   
10                 $189

## Figure 1: Net Income Under Different Tax Policies

In [30]:
# Create a figure comparing net income across policies
fig1 = px.bar(
    results_df,
    x="income",
    y=["current_law_net_income", "current_policy_net_income", "current_policy_50k_net_income"],
    barmode="group",
    facet_col="state",
    facet_col_wrap=2,
    labels={
        "income": "Household Income ($)",
        "value": "Net Income ($)",
        "variable": "Policy"
    },
    title="Net Income Under Different Tax Policies",
    color_discrete_map={
        "current_law_net_income": "#1f77b4",
        "current_policy_net_income": "#ff7f0e",
        "current_policy_50k_net_income": "#2ca02c"
    }
)

# Improve legend labels
newnames = {
    'current_law_net_income': 'Current Law', 
    'current_policy_net_income': 'Current Policy (SALT cap $10k)', 
    'current_policy_50k_net_income': 'Current Policy (SALT cap $50k MFJ/$25k Single)'
}
fig1.for_each_trace(lambda t: t.update(name=newnames[t.name]))

# Format axes as currency
fig1.update_xaxes(tickprefix="$", tickformat=",.0f")
fig1.update_yaxes(tickprefix="$", tickformat=",.0f")

fig1.show()

## Figure 2: Effective SALT Cap Analysis

In [23]:
# Function to calculate effective SALT cap for varying property tax levels
def calculate_effective_salt_cap(state, income, reform):
    situation = {
        "people": {
            "you": {
                "age": {2026: 40},
                "employment_income": {2026: income},
            },
            "your partner": {"age": {2026: 40}},
        },
        "families": {"your family": {"members": ["you", "your partner"]}},
        "tax_units": {"your tax unit": {"members": ["you", "your partner"]}},
        "spm_units": {"your household": {"members": ["you", "your partner"]}},
        "households": {
            "your household": {
                "members": ["you", "your partner"],
                "state_name": {2026: state},
            }
        },
        # Set up the axis for property taxes
        "axes": [
            [{"name": "real_estate_taxes", "count": 1201, "min": -20000, "max": 100000}]
        ],
    }
    
    simulation = Simulation(situation=situation, reform=reform)
    
    # Calculate values along the axis
    property_taxes_axis = simulation.calculate("real_estate_taxes", map_to = "household", period =2026)
    regular_tax = simulation.calculate("regular_tax_before_credits", map_to = "household", period =2026)
    amt = simulation.calculate("amt_base_tax", map_to = "household", period =2026)
    salt_deduction = simulation.calculate("salt_deduction", map_to = "household", period =2026)
    sales_tax = simulation.calculate("state_sales_tax", period =2026)
    
        # Create DataFrame with data
    effective_caps = pd.DataFrame({
        "property_tax": property_taxes_axis,
        "regular_tax": regular_tax,
        "amt": amt,
        "salt_deduction": salt_deduction,
        "sales_tax": sales_tax,
        "amt_binds": amt > regular_tax
    })
    return effective_caps

In [ ]:
# Calculate effective SALT caps for each state and income level
effective_cap_data = []

for state in states:
    for income in income_levels:
        print(f"\nAnalyzing state {state} with income {income}")
        
        # Calculate for current law
        current_law_caps = calculate_effective_salt_cap(state, income, baseline_brachning_reform)
        current_law_caps['policy'] = 'Current Law'
        current_law_caps['state'] = state
        current_law_caps['income'] = income
        
        # Calculate for current policy
        current_policy_caps = calculate_effective_salt_cap(state, income, current_policy)
        current_policy_caps['policy'] = 'Current Policy'
        current_policy_caps['state'] = state
        current_policy_caps['income'] = income

        
        
        effective_cap_data.append(current_law_caps)
        effective_cap_data.append(current_policy_caps)

# Combine into a single DataFrame
effective_cap_df = pd.concat(effective_cap_data, ignore_index=True)
effective_cap_df.head()


Analyzing state NY with income 250000

Analyzing state NY with income 500000


In [ ]:
import matplotlib.pyplot as plt
import seaborn as sns
import pandas as pd
import numpy as np
from matplotlib.ticker import StrMethodFormatter
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Assuming your DataFrame is already created and called effective_cap_df
# Let's create a plot for each state

# Get unique states
states = effective_cap_df['state'].unique()

# Create interactive Plotly visualization
fig = make_subplots(rows=len(states), cols=1, 
                    subplot_titles=[f"State: {state}" for state in states],
                    vertical_spacing=0.1,
                    shared_xaxes=True)

# Colors for different policies
colors = {'Current Law': 'blue', 'Current Policy': 'red'}

# For each state, create a plot
for i, state in enumerate(states):
    state_data = effective_cap_df[effective_cap_df['state'] == state]
    
    # Group by policy and income to get different lines
    for policy in state_data['policy'].unique():
        for income in state_data['income'].unique():
            filter_data = state_data[(state_data['policy'] == policy) & 
                                    (state_data['income'] == income)]
            
            # Sort by property tax to ensure lines are connected properly
            filter_data = filter_data.sort_values('property_tax')
            
            # Add regular tax line
            fig.add_trace(
                go.Scatter(
                    x=filter_data['property_tax'],
                    y=filter_data['regular_tax'],
                    mode='lines',
                    name=f"{policy} - Regular Tax (Income: ${income:,})",
                    line=dict(color=colors[policy]),
                    hovertemplate="<b>%{fullData.name}</b><br>" +
                                 "Property Tax: $%{x:,.2f}<br>" +
                                 "Regular Tax: $%{y:,.2f}<br>" +
                                 "SALT Deduction: $%{customdata[0]:,.2f}<br>" +
                                 "Sales Tax: $%{customdata[1]:,.2f}<br>",
                    customdata=np.stack((filter_data['salt_deduction'], 
                                        filter_data['sales_tax']), axis=1),
                    legendgroup=f"{policy}-{income}-regular",
                    showlegend=i==0  # Only show in legend for first state
                ),
                row=i+1, col=1
            )
            
            # Add AMT line
            fig.add_trace(
                go.Scatter(
                    x=filter_data['property_tax'],
                    y=filter_data['amt'],
                    mode='lines',
                    name=f"{policy} - AMT (Income: ${income:,})",
                    line=dict(color=colors[policy], dash='dash'),
                    hovertemplate="<b>%{fullData.name}</b><br>" +
                                 "Property Tax: $%{x:,.2f}<br>" +
                                 "AMT: $%{y:,.2f}<br>" +
                                 "SALT Deduction: $%{customdata[0]:,.2f}<br>" +
                                 "Sales Tax: $%{customdata[1]:,.2f}<br>",
                    customdata=np.stack((filter_data['salt_deduction'], 
                                        filter_data['sales_tax']), axis=1),
                    legendgroup=f"{policy}-{income}-amt",
                    showlegend=i==0  # Only show in legend for first state
                ),
                row=i+1, col=1
            )

# Update layout
fig.update_layout(
    height=300*len(states),
    width=1000,
    title_text="Tax Liability by Property Tax for Different States",
    legend_title="Tax Type",
    template="plotly_white",
    hovermode="closest"
)

# Update axes
fig.update_xaxes(title_text="Property Tax ($)", tickprefix="$", tickformat=",.2f")
fig.update_yaxes(title_text="Tax Liability ($)", tickprefix="$", tickformat=",.2f")

# Show figure
fig.show()

In [22]:
def find_first_binding_points_current_law(df):
    # Create an empty list to store the results
    binding_points = []
    
    # Filter for Current Law only
    current_law_df = df[df['policy'] == 'Current Law']
    
    # Get unique combinations of state and income
    combinations = current_law_df.groupby(['state', 'income']).groups.keys()
    
    for state, income in combinations:
        # Filter data for this combination
        subset = current_law_df[(current_law_df['state'] == state) & 
                               (current_law_df['income'] == income)]
        
        # Sort by property_tax to ensure we find the earliest point
        subset = subset.sort_values('property_tax')
        
        # Find the first row where binds is True
        first_binding = subset[subset['amt_binds'] == True]
        
        if not first_binding.empty:
            # Get the first row where binding occurs
            binding_row = first_binding.iloc[0]
            binding_points.append(binding_row)
        else:
            # If no binding occurs, we can either skip or include a placeholder
            print(f"No binding found for {state}, income ${income} under Current Law")
    
    # Convert the list to a DataFrame
    if binding_points:
        binding_df = pd.DataFrame(binding_points)
        return binding_df
    else:
        return pd.DataFrame()

# Apply the function to your dataframe
first_binding_points = find_first_binding_points_current_law(effective_cap_df)

# Display the results
print("First AMT binding points for each state and income level (Current Law only):")
display(first_binding_points)

# Format for better readability
formatted_results = first_binding_points[['state', 'income', 'property_tax', 
                                         'regular_tax', 'amt', 'salt_deduction', 
                                         'sales_tax', 'amt_binds']]
formatted_results = formatted_results.sort_values(['state', 'income'])

# Create a more readable table
def format_currency(val):
    return f"${val:,.2f}" if isinstance(val, (int, float)) else val

readable_results = formatted_results.copy()
for col in ['property_tax', 'regular_tax', 'amt', 'salt_deduction', 'sales_tax', 'income']:
    if col in readable_results.columns:
        readable_results[col] = readable_results[col].apply(format_currency)

print("\nFormatted binding points table (Current Law only):")
display(readable_results)

No binding found for CA, income $250000, policy Current Policy
No binding found for CA, income $500000, policy Current Policy
No binding found for CA, income $750000, policy Current Policy
No binding found for CA, income $1000000, policy Current Policy
No binding found for NJ, income $250000, policy Current Policy
No binding found for NJ, income $500000, policy Current Policy
No binding found for NJ, income $750000, policy Current Policy
No binding found for NJ, income $1000000, policy Current Policy
No binding found for NY, income $250000, policy Current Policy
No binding found for NY, income $500000, policy Current Policy
No binding found for NY, income $750000, policy Current Policy
No binding found for NY, income $1000000, policy Current Policy
No binding found for PA, income $250000, policy Current Policy
No binding found for PA, income $500000, policy Current Policy
No binding found for PA, income $750000, policy Current Policy
No binding found for PA, income $1000000, policy Cur

property_tax    regular_tax       amt  salt_deduction    sales_tax  \
16208  19809.025391   39079.476562   39104.0    38955.437500  2113.094971   
18018      0.000000  117348.929688  124732.0    44051.156250  2638.625732   
20020      0.000000  197189.750000  205120.0    72301.156250  2638.625732   
22241  22594.667969  275081.593750  275120.0   125604.562500  2638.625732   
8252   25173.968750   39092.476562   39104.0    38909.019531  2019.837769   
10010      0.000000  122097.992188  124732.0    29660.050781  2524.522949   
12015    309.516022  205083.046875  205120.0    52368.566406  2524.522949   
14509  51070.140625  275101.531250  275120.0   125554.187500  2524.522949   
240    24761.281250   39084.046875   39104.0    38939.132812  2184.409180   
2002       0.000000  121555.875000  124732.0    31302.849609  2769.185547   
4042    3920.536133  205091.046875  205120.0    52348.386719  2769.185547   
6588   60046.105469  275083.812500  275120.0   125598.953125  2769.185547   
24327  31261.117188   39084.886719   39104.0    38936.117188  1677.529663   
26088   6396.664062  124709.421875  124732.0    21746.664062  2097.734863   
28312  29300.849609  205099.953125  205120.0    52325.851562  2097.734863   
30949  94815.070312  275117.031250  275120.0   125515.070312  2097.734863   

       amt_binds       policy state   income  
16208       True  Current Law    CA   250000  
18018       True  Current Law    CA   500000  
20020       True  Current Law    CA   750000  
22241       True  Current Law    CA  1000000  
8252        True  Current Law    NJ   250000  
10010       True  Current Law    NJ   500000  
12015       True  Current Law    NJ   750000  
14509       True  Current Law    NJ  1000000  
240         True  Current Law    NY   250000  
2002        True  Current Law    NY   500000  
4042        True  Current Law    NY   750000  
6588        True  Current Law    NY  1000000  
24327       True  Current Law    PA   250000  
26088       True  Current Law    PA   500000  
28312       True  Current Law    PA   750000  
30949       True  Current Law    PA  1000000


Formatted binding points table:


state         income       policy property_tax  regular_tax  \
16208    CA    $250,000.00  Current Law   $19,809.03   $39,079.48   
18018    CA    $500,000.00  Current Law        $0.00  $117,348.93   
20020    CA    $750,000.00  Current Law        $0.00  $197,189.75   
22241    CA  $1,000,000.00  Current Law   $22,594.67  $275,081.59   
8252     NJ    $250,000.00  Current Law   $25,173.97   $39,092.48   
10010    NJ    $500,000.00  Current Law        $0.00  $122,097.99   
12015    NJ    $750,000.00  Current Law      $309.52  $205,083.05   
14509    NJ  $1,000,000.00  Current Law   $51,070.14  $275,101.53   
240      NY    $250,000.00  Current Law   $24,761.28   $39,084.05   
2002     NY    $500,000.00  Current Law        $0.00  $121,555.88   
4042     NY    $750,000.00  Current Law    $3,920.54  $205,091.05   
6588     NY  $1,000,000.00  Current Law   $60,046.11  $275,083.81   
24327    PA    $250,000.00  Current Law   $31,261.12   $39,084.89   
26088    PA    $500,000.00  Current Law    $6,396.66  $124,709.42   
28312    PA    $750,000.00  Current Law   $29,300.85  $205,099.95   
30949    PA  $1,000,000.00  Current Law   $94,815.07  $275,117.03   

               amt salt_deduction  sales_tax  amt_binds  
16208   $39,104.00     $38,955.44  $2,113.09       True  
18018  $124,732.00     $44,051.16  $2,638.63       True  
20020  $205,120.00     $72,301.16  $2,638.63       True  
22241  $275,120.00    $125,604.56  $2,638.63       True  
8252    $39,104.00     $38,909.02  $2,019.84       True  
10010  $124,732.00     $29,660.05  $2,524.52       True  
12015  $205,120.00     $52,368.57  $2,524.52       True  
14509  $275,120.00    $125,554.19  $2,524.52       True  
240     $39,104.00     $38,939.13  $2,184.41       True  
2002   $124,732.00     $31,302.85  $2,769.19       True  
4042   $205,120.00     $52,348.39  $2,769.19       True  
6588   $275,120.00    $125,598.95  $2,769.19       True  
24327   $39,104.00     $38,936.12  $1,677.53       True  
26088  $124,732.00     $21,746.66  $2,097.73       True  
28312  $205,120.00     $52,325.85  $2,097.73       True  
30949  $275,120.00    $125,515.07  $2,097.73       True

In [17]:
# Create a figure showing effective SALT cap comparison
fig2 = px.line(
    effective_cap_df,
    x="property_tax",
    y="regular_tax",
    color="policy",
    line_dash="policy",
    facet_col="state",
    facet_row="income",
    labels={
        "property_tax": "Property Tax ($)",
        "regular_tax": "Regular Tax Before Credits ($)",
        "policy": "Policy"
    },
    title="Effective SALT Cap Comparison",
    color_discrete_map={
        "Current Law": "#1f77b4",
        "Current Policy": "#ff7f0e"
    }
)

# Add AMT lines
for state in states:
    for income in income_levels:
        for policy in ["Current Law", "Current Policy"]:
            subset = effective_cap_df[
                (effective_cap_df["state"] == state) & 
                (effective_cap_df["income"] == income) &
                (effective_cap_df["policy"] == policy)
            ]
            fig2.add_scatter(
                x=subset["property_tax"],
                y=subset["amt"],
                mode="lines",
                line=dict(dash="dot", color="red" if policy == "Current Law" else "orange"),
                name=f"{policy} AMT",
                showlegend=False,
                row=income_levels.index(income) + 1,
                col=states.index(state) + 1
            )

# Format axes as currency
fig2.update_xaxes(tickprefix="$", tickformat=",.0f")
fig2.update_yaxes(tickprefix="$", tickformat=",.0f")

# Update facet row titles to show income
for i, income in enumerate(income_levels):
    fig2.layout.annotations[i*len(states)].text = f"Income: ${income:,}"

fig2.show()

IndexError: tuple index out of range

## Figure 3: Effective SALT Cap by State

In [34]:
# Create a figure for each state showing how the effective cap changes with income
for state in states:
    fig3 = go.Figure()
    
    for income in income_levels:
        # Current law data
        cl_data = effective_cap_df[
            (effective_cap_df["state"] == state) & 
            (effective_cap_df["income"] == income) &
            (effective_cap_df["policy"] == "Current Law")
        ]
        
        # Current policy data
        cp_data = effective_cap_df[
            (effective_cap_df["state"] == state) & 
            (effective_cap_df["income"] == income) &
            (effective_cap_df["policy"] == "Current Policy")
        ]
        
        # Add regular tax lines
        fig3.add_trace(go.Scatter(
            x=cl_data["property_tax"],
            y=cl_data["regular_tax"],
            mode="lines",
            name=f"Income ${income:,} - Current Law Regular Tax",
            line=dict(color=px.colors.qualitative.Plotly[income_levels.index(income)]),
        ))
        
        fig3.add_trace(go.Scatter(
            x=cp_data["property_tax"],
            y=cp_data["regular_tax"],
            mode="lines",
            line=dict(dash="dash", color=px.colors.qualitative.Plotly[income_levels.index(income)]),
            name=f"Income ${income:,} - Current Policy Regular Tax",
        ))
        
        # Add AMT lines
        fig3.add_trace(go.Scatter(
            x=cl_data["property_tax"],
            y=cl_data["amt"],
            mode="lines",
            line=dict(dash="dot", color=px.colors.qualitative.Plotly[income_levels.index(income)]),
            name=f"Income ${income:,} - Current Law AMT",
            showlegend=False,
        ))
        
        fig3.add_trace(go.Scatter(
            x=cp_data["property_tax"],
            y=cp_data["amt"],
            mode="lines",
            line=dict(dash="longdash", color=px.colors.qualitative.Plotly[income_levels.index(income)]),
            name=f"Income ${income:,} - Current Policy AMT",
            showlegend=False,
        ))
    
    # Add a vertical line at the 10k SALT cap
    fig3.add_vline(x=10000, line_dash="dash", line_color="red", annotation_text="$10k SALT Cap")
    
    # Format the figure
    fig3.update_layout(
        title=f"Effective SALT Cap for {state} at Different Income Levels",
        xaxis_title="Property Tax ($)",
        yaxis_title="Tax Amount ($)",
        legend_title="Income & Policy",
        xaxis=dict(tickprefix="$", tickformat=",.0f"),
        yaxis=dict(tickprefix="$", tickformat=",.0f"),
    )
    
    fig3.show()

## Summary Tables

In [18]:
# Create a summary table of net income under each policy
summary_table = results_df.pivot_table(
    index=["state", "income"],
    values=["current_law_net_income", "current_policy_net_income", "current_policy_50k_net_income"]
)

# Add columns for differences between policies
summary_table["current_policy_vs_law_diff"] = summary_table["current_policy_net_income"] - summary_table["current_law_net_income"]
summary_table["current_policy_50k_vs_law_diff"] = summary_table["current_policy_50k_net_income"] - summary_table["current_law_net_income"]
summary_table["current_policy_50k_vs_policy_diff"] = summary_table["current_policy_50k_net_income"] - summary_table["current_policy_net_income"]

# Format as dollars
pd.options.display.float_format = '${:,.2f}'.format

summary_table

current_law_net_income  current_policy_50k_net_income  \
state income                                                           
CA    250000              $178,649.25                    $182,034.25   
      500000              $317,125.12                    $344,640.12   
      750000              $457,086.12                    $479,331.12   
      1000000             $604,368.94                    $605,456.44   
NJ    250000              $180,813.34                    $185,713.53   
      500000              $327,511.41                    $355,026.41   
      750000              $469,265.41                    $491,510.41   
      1000000             $618,580.12                    $622,052.88   
NY    250000              $177,939.05                    $182,715.25   
      500000              $321,527.69                    $349,042.69   
      750000              $468,910.31                    $491,155.31   
      1000000             $620,758.88                    $627,768.44   
PA    250000              $182,460.00                    $189,057.00   
      500000              $338,786.00                    $362,413.00   
      750000              $494,848.00                    $517,093.00   
      1000000             $641,574.19                    $662,385.50   

               current_policy_net_income  current_policy_vs_law_diff  \
state income                                                           
CA    250000                 $182,034.25                   $3,385.00   
      500000                 $338,432.12                  $21,307.00   
      750000                 $472,541.12                  $15,455.00   
      1000000                $598,278.44                  $-6,090.50   
NJ    250000                 $185,713.53                   $4,900.19   
      500000                 $348,818.41                  $21,307.00   
      750000                 $484,720.41                  $15,455.00   
      1000000                $614,874.88                  $-3,705.25   
NY    250000                 $182,715.25                   $4,776.20   
      500000                 $342,834.69                  $21,307.00   
      750000                 $484,365.31                  $15,455.00   
      1000000                $620,590.44                    $-168.44   
PA    250000                 $189,057.00                   $6,597.00   
      500000                 $360,093.00                  $21,307.00   
      750000                 $510,303.00                  $15,455.00   
      1000000                $655,207.50                  $13,633.31   

               current_policy_50k_vs_law_diff  \
state income                                    
CA    250000                        $3,385.00   
      500000                       $27,515.00   
      750000                       $22,245.00   
      1000000                       $1,087.50   
NJ    250000                        $4,900.19   
      500000                       $27,515.00   
      750000                       $22,245.00   
      1000000                       $3,472.75   
NY    250000                        $4,776.20   
      500000                       $27,515.00   
      750000                       $22,245.00   
      1000000                       $7,009.56   
PA    250000                        $6,597.00   
      500000                       $23,627.00   
      750000                       $22,245.00   
      1000000                      $20,811.31   

               current_policy_50k_vs_policy_diff  
state income                                      
CA    250000                               $0.00  
      500000                           $6,208.00  
      750000                           $6,790.00  
      1000000                          $7,178.00  
NJ    250000                               $0.00  
      500000                           $6,208.00  
      750000                           $6,790.00  
      1000000                          $7,178.00  
NY    250000                

In [19]:
# Create a summary table of SALT deduction under each policy
salt_table = results_df.pivot_table(
    index=["state", "income"],
    values=["current_law_salt_deduction", "current_policy_salt_deduction", "current_policy_50k_salt_deduction"]
)

salt_table

current_law_salt_deduction  current_policy_50k_salt_deduction  \
state income                                                                   
CA    250000                   $30,396.41                         $30,396.41   
      500000                   $66,551.16                         $50,000.00   
      750000                  $106,051.16                         $50,000.00   
      1000000                 $148,009.89                         $50,000.00   
NJ    250000                   $24,985.05                         $24,985.05   
      500000                   $52,160.05                         $50,000.00   
      750000                   $85,809.05                         $50,000.00   
      1000000                 $119,484.05                         $50,000.00   
NY    250000                   $25,427.85                         $25,427.85   
      500000                   $53,802.85                         $50,000.00   
      750000                   $82,177.85                         $50,000.00   
      1000000                 $110,552.85                         $50,000.00   
PA    250000                   $18,925.00                         $18,925.00   
      500000                   $37,850.00                         $37,850.00   
      750000                   $56,775.00                         $50,000.00   
      1000000                  $75,700.00                         $50,000.00   

               current_policy_salt_deduction  
state income                                  
CA    250000                      $10,000.00  
      500000                      $10,000.00  
      750000                      $10,000.00  
      1000000                     $10,000.00  
NJ    250000                      $10,000.00  
      500000                      $10,000.00  
      750000                      $10,000.00  
      1000000                     $10,000.00  
NY    250000                      $10,000.00  
      500000                      $10,000.00  
      750000                      $10,000.00  
      1000000                     $10,000.00  
PA    250000                      $10,000.00  
      500000                      $10,000.00  
      750000                      $10,000.00  
      1000000                     $10,000.00